# Searching for machine learning models using semantic search

> Finding models on the Hugging Face hub using semantic search

- toc: true 
- badges: false
- comments: true
- categories: [huggingface, huggingface-datasets, semantic-search]
- search_exclude: false
- badges: true
- image: https://github.com/davanstrien/blog/blob/master/images/hub_model_search.webp?raw=true

The [Hugging Face model hub](https://huggingface.co/models) has (at the time of the last checking) 60,509 models publicly available. Some of these models are useful as base models for further fine-tuning; these include your classics like `bert-base-uncased`. 

The hub also has more obscure indie hits that might already do a good job on your desired downstream task or be a closer start. For example, if one wanted to classify the genre of 18th Century books, it might make sense to start with [a model for classifying 19th Century books](https://huggingface.co/BritishLibraryLabs/bl-books-genre). 

## Finding candidate models

Ideally, we'd like a quick way to identify if a model might already do close to what we want. From there, we would likely want to review a bunch of other info about the model before deciding if it might be helpful for us or not. 

Unfortunately, finding suitable models on the hub isn't always that easy. Even knowing that models for genre classification exist on the hub, we don't find any results.

![](https://github.com/davanstrien/blog/blob/master/images/hub_model_search.webp?raw=1)

It's not documented exactly how the search on the hub works, but it seems to be based mainly on the model's name rather than the README or other information. In this blog post, I will continue some [previous experiments with embeddings](https://danielvanstrien.xyz/metadata/deployment/huggingface/ethics/huggingface-datasets/faiss/2022/01/13/image_search.html) to see if there might be different ways in which we could identify potential models. 

This will be a very rough experiment and is more about establishing whether this is an avenue worth exploring rather than a fully fleshed-out approach. 

First install some libraries we'll use:

In [1]:
import torch

In [2]:
deps = ["datasets" ,"sentence-transformers", "rich['jupyter']", "requests"]
if torch.cuda.is_available():
    deps.append("faiss-gpu")
else:
    deps.append("faise-cpu")

In [3]:
%%capture
!pip install {" ".join(deps)} --upgrade

In [4]:
!git config --global credential.helper store

These days I almost always have the rich extension loaded!

In [5]:
%load_ext rich

## Using the huggingface_hub API to download some model metadata 

Our goal is to see if we might be able to find suitable models more efficiently using some form of semantic search (i.e. using embeddings). To do this, we should grab some model data from the hub. The easiest way to do this is using the hub API.  

In [6]:
from huggingface_hub import hf_api
import re
from rich import print

In [7]:
api = hf_api.HfApi()

In [8]:
api

<huggingface_hub.hf_api.HfApi object at 0x7f976cf7fee0>

We can take a look at some example models

In [9]:
all_models = api.list_models()
all_models[:3]

/usr/local/lib/python3.8/dist-packages/huggingface_hub/utils/_deprecation.py:233: FutureWarning: 'list_models' currently returns a list of objects but is planned to be a generator starting from version 0.14 in order to implement pagination. Please avoid to use `list_models(...).__getitem__` or explicitly convert the output to a list first with `list(iter(list_models)(...))`.
  warnings.warn(self._deprecation_msg.format(attr_name=attr_name), FutureWarning)


[
    ModelInfo: {
        modelId: albert-base-v1
        sha: None
        lastModified: None
        tags: None
        pipeline_tag: fill-mask
        siblings: []
        private: False
        author: None
        config: None
        securityStatus: None
        _id: 621ffdc036468d709f174328
        id: albert-base-v1
},
    ModelInfo: {
        modelId: albert-base-v2
        sha: None
        lastModified: None
        tags: None
        pipeline_tag: fill-mask
        siblings: []
        private: False
        author: None
        config: None
        securityStatus: None
        _id: 621ffdc036468d709f174329
        id: albert-base-v2
},
    ModelInfo: {
        modelId: albert-large-v1
        sha: None
        lastModified: None
        tags: None
        pipeline_tag: fill-mask
        siblings: []
        private: False
        author: None
        config: None
        securityStatus: None
        _id: 621ffdc036468d709f17432a
        id: albert-large-v1
}
]

For a particular model we can also see what files there are. 

In [10]:
files = api.list_repo_files(all_models[0].modelId)

In [11]:
files

[
    '.gitattributes',
    'README.md',
    'config.json',
    'pytorch_model.bin',
    'spiece.model',
    'tf_model.h5',
    'tokenizer.json',
    'with-prefix-tf_model.h5'
]

### Filtering 

To limit the scope of this blog post, we'll focus only on Pytorch models and 'text classification' models. The metadata about the model type is likely usually pretty reliable. The model task metadata, on the other hand, is not always reliable in my experience. This means we probably have some models that aren't text-classification models and don't include some actual text classification models in our dataset. For now, we won't worry too much about this. 

In [12]:
from huggingface_hub import ModelSearchArguments

In [13]:
model_args = ModelSearchArguments()

In [14]:
from huggingface_hub import ModelFilter

model_filter = ModelFilter(
    task=model_args.pipeline_tag.TextClassification, 
    library=model_args.library.PyTorch
)
api.list_models(filter=model_filter)[0]

ModelInfo: {
        modelId: distilbert-base-uncased-finetuned-sst-2-english
        sha: bfdd146ea2b6807255b73527f1327ca12b6ed5c4
        lastModified: 2022-12-05T13:55:22.000Z
        tags: ['pytorch', 'tf', 'rust', 'safetensors', 'distilbert', 'text-classification', 'en', 'dataset:sst2', 'dataset:glue', 'doi:10.57967/hf/0181', 'transformers', 'license:apache-2.0', 'model-index', 'has_space']
        pipeline_tag: text-classification
        siblings: [RepoFile(rfilename='.gitattributes', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='README.md', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='config.json', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='map.jpeg', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='model.safetensors', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='pytorch_model.bin', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='rust_model.ot', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='tf_model.h5', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='tokenizer_config.json', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='vocab.txt', size='None', blob_id='None', lfs='None')]
        private: False
        author: None
        config: None
        securityStatus: None
        _id: 621ffdc036468d709f174346
        id: distilbert-base-uncased-finetuned-sst-2-english
        likes: 138
        downloads: 5620960
        library_name: transformers
}

Now we have a filter we'll use that to grab all the models that match this filter.  

In [15]:
all_models = api.list_models(filter=model_filter)

In [16]:
all_models[0]

ModelInfo: {
        modelId: distilbert-base-uncased-finetuned-sst-2-english
        sha: bfdd146ea2b6807255b73527f1327ca12b6ed5c4
        lastModified: 2022-12-05T13:55:22.000Z
        tags: ['pytorch', 'tf', 'rust', 'safetensors', 'distilbert', 'text-classification', 'en', 'dataset:sst2', 'dataset:glue', 'doi:10.57967/hf/0181', 'transformers', 'license:apache-2.0', 'model-index', 'has_space']
        pipeline_tag: text-classification
        siblings: [RepoFile(rfilename='.gitattributes', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='README.md', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='config.json', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='map.jpeg', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='model.safetensors', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='pytorch_model.bin', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='rust_model.ot', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='tf_model.h5', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='tokenizer_config.json', size='None', blob_id='None', lfs='None'), RepoFile(rfilename='vocab.txt', size='None', blob_id='None', lfs='None')]
        private: False
        author: None
        config: None
        securityStatus: None
        _id: 621ffdc036468d709f174346
        id: distilbert-base-uncased-finetuned-sst-2-english
        likes: 138
        downloads: 5620960
        library_name: transformers
}

Let's see how many models that gives us. 

In [17]:
len(all_models)

/usr/local/lib/python3.8/dist-packages/huggingface_hub/utils/_deprecation.py:233: FutureWarning: 'list_models' currently returns a list of objects but is planned to be a generator starting from version 0.14 in order to implement pagination. Please avoid to use `list_models(...).__len__` or explicitly convert the output to a list first with `list(iter(list_models)(...))`.
  warnings.warn(self._deprecation_msg.format(attr_name=attr_name), FutureWarning)


13141

Later on, in this blog, we'll want to work with the `config.json` files (we'll get back to why later!), so we'll quickly check that all our models have this. 

In [18]:
def has_config(model):
    has_config = False
    files = model.siblings
    for file in files:
        if "config.json" in file.rfilename:
            has_config = True
            return has_config
        else:
            continue

In [19]:
has_config(all_models[0])

True

In [20]:
has_config = [model for model in all_models if has_config(model)]

Let's check how many we have now

In [21]:
len(has_config)

13135

We can also download a particular file from the hub 

In [22]:
from huggingface_hub import hf_hub_download
file = hf_hub_download(repo_id=all_models[0].modelId, filename="config.json")

In [23]:
file

'/root/.cache/huggingface/hub/models--distilbert-base-uncased-finetuned-sst-2-english/snapshots/bfdd146ea2b6807255b73527f1327ca12b6ed5c4/config.json'

In [24]:
import json
with open(file) as f:
    data = json.load(f)

In [25]:
data

{
    'activation': 'gelu',
    'architectures': ['DistilBertForSequenceClassification'],
    'attention_dropout': 0.1,
    'dim': 768,
    'dropout': 0.1,
    'finetuning_task': 'sst-2',
    'hidden_dim': 3072,
    'id2label': {'0': 'NEGATIVE', '1': 'POSITIVE'},
    'initializer_range': 0.02,
    'label2id': {'NEGATIVE': 0, 'POSITIVE': 1},
    'max_position_embeddings': 512,
    'model_type': 'distilbert',
    'n_heads': 12,
    'n_layers': 6,
    'output_past': True,
    'pad_token_id': 0,
    'qa_dropout': 0.1,
    'seq_classif_dropout': 0.2,
    'sinusoidal_pos_embds': False,
    'tie_weights_': True,
    'vocab_size': 30522
}

We can also check if the model has a `README.md`

In [26]:
def has_file_in_repo(model,file_name):
    has_file = False
    files = model.siblings
    for file in files:
        if file_name in file.rfilename:
            has_file = True
            return has_file
        else:
            continue    

In [27]:
has_file_in_repo(has_config[0],'README.md')

True

In [28]:
has_readme = [model for model in has_config if has_file_in_repo(model,"README.md")]

We can see that there are more configs than READMEs

In [29]:
len(has_readme)

7825

In [30]:
len(has_config)

13135

We now write some functions to grab both the `README.md` and `config.json` files from the hub. 

In [31]:
from requests.exceptions import JSONDecodeError
import concurrent.futures

In [32]:
from tqdm.auto import tqdm

## Semantic search of model cards

We now get to the main point of all of this. Can we use semantic search to try and find models of interest? For this, we'll use the sentence-transformers library. This blog won't cover all the background of this library. The [docs](https://www.sbert.net/index.html) give a helpful overview and some tutorials. 

To start, we'll see if we can search using the information in the `README.md`. This should, in theory, contain data that might be similar to the kinds of things we want to search for when finding candidate models. We might prefer to use semantic search over an exact match because the terms we use might be different, or there is a related concept/model that might be close enough to make it worthwhile for fine-tuning. 


First, we import the `SentenceTransformer` class and some util functions. 

In [33]:
from datasets import load_dataset
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [53]:
!pip install markdown
!pip install bs4
import re
import markdown # pip install markdown
from bs4 import BeautifulSoup # pip install beautifulsoup4

def md_to_text(md):
    html = markdown.markdown(md)
    soup = BeautifulSoup(html, features='html.parser')
    return str(soup.get_text())

from datasets import Dataset
import pandas as pd
ds_longer_readmes = []
with open('/content/drive/MyDrive/npm_packages_readmes.ljson') as f:
  for line in f:
    if (len(line) > 100):
      package = json.loads(line)
      package['readme'] = re.sub(pattern = '```.*?```', repl = '', string = package['readme'], flags = re.MULTILINE | re.DOTALL)
      #package['readme'] = md_to_text(package['readme'])
      ds_longer_readmes.append(package)

df = pd.DataFrame(data=ds_longer_readmes)
ds = Dataset.from_pandas(df)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


We'll now download an embedding model. There are many we could choose from but since we're just trying things out at the moment we won't stress about the particular model we use here. 

In [35]:
from sentence_transformers import SentenceTransformer, util
model = SentenceTransformer('all-mpnet-base-v2')

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


Moving 0 files to the new cache system


0it [00:00, ?it/s]

Let's start on longer README's, here i mean a long readme that is just not super short... 

We now create embeddings for the `readme` column and store this in a new `embedding` column  

In [36]:
def encode_readme(readme):
    return model.encode(readme,device='cuda')

In [54]:
ds_with_embeddings = ds.map(lambda example: 
                                           {"embedding":encode_readme(example['readme'])},batched=True, batch_size=16)
                                                                      

  0%|          | 0/22763 [00:00<?, ?ba/s]

In [55]:
ds_with_embeddings

Dataset({
    features: ['name', 'readme', 'maintainers', 'description', 'embedding'],
    num_rows: 364205
})

We can now use the `add_fais_index` to create an index which allows us to efficiently query these embeddings 

In [56]:
ds_with_embeddings.add_faiss_index(column='embedding')

  0%|          | 0/365 [00:00<?, ?it/s]

Dataset({
    features: ['name', 'readme', 'maintainers', 'description', 'embedding'],
    num_rows: 364205
})

### Similar models

To start, we'll take a readme for a model and see how well the model performs on finding similar models.

In [57]:
def find(lst, predicate):
     return next(i for i, j in enumerate(lst) if predicate(j))

query_readme = ds_with_embeddings[find(ds_with_embeddings, lambda x: 'As developers start to depend on your library, you may encounter issues such as' in x["readme"])]["readme"]

In [58]:
print(query_readme)

@microsoft/api-extractor



&nbsp;&nbsp;&nbsp;&nbsp;&nbsp; https://api-extractor.com/





API Extractor helps you build better TypeScript library packages.  Suppose for example that your company has 
published an NPM package called "awesome-widgets" that exports many classes and interfaces.  As developers start to
depend on your library, you may encounter issues such as...


Accidental breaks:  People keep reporting that their code won't compile after a supposedly "minor" update.  To 
address this, you boldly propose that every awesome-widgets pull request must be approved by an experienced 
developer from your team.  But that proves unrealistic -- nobody has time to look at every single PR!  What you 
really need is a way to detect PRs that change API contracts, and flag them for review.  That would focus attention
in the right place... but how to do that?
Missing exports: Suppose the awesome-widgets package exports an API function AwesomeButton.draw() that requires a 
parameter of type DrawStyle, but you forgot to export this enum.  Things seem fine at first, but when a developer 
tries to call that function, they discover that there's no way to specify the DrawStyle.  How to avoid these 
oversights?
Accidental exports: You meant for your DrawHelper class to be kept internal, but one day you realize it's being 
exported.  When you try to remove it, consumers complain that they're using it.  How do we avoid this in the 
future?
Alpha/Beta graduation:  You want to release previews of new APIs that are not ready for prime time yet.  But if you
did a major SemVer bump every time these definitions evolve, the villagers would be after you with torches and 
pitchforks!  A better approach is to designate certain classes/members as alpha quality, then promote them to beta 
and finally to public as they mature.  But how to indicate this to your consumers?  (And how to detect scoping 
mistakes?  A public function should never return a beta result.)
*.d.ts rollup: You webpacked your library into a nice *.js bundle file -- so why ship your typings as a messy tree 
of lib/*.d.ts files full of private definitions?  Can't we consolidate them into a tidy *.d.ts rollup file?  And if
you publish internal/beta/public releases, each release type should get its own *.d.ts file with appropriate 
trimming.  Developers building a production project don't want to see a bunch of internal and beta members in their
VS Code IntelliSense!
Online documentation:  You have faithfully annotated each TypeScript member with nice TSDoc descriptions.  Now that
your library has shipped, it's time to set up a nicely formatted API reference.  What tool to use?


API Extractor provides an integrated, professional-quality solution for all these problems.  It is invoked at build
time by your toolchain and leverages the TypeScript compiler engine to:


Detect a project's exported API surface
Capture the contracts in a concise report designed to facilitate review
Warn about common mistakes (e.g. missing exports, inconsistent visibility, etc.)
Generate *.d.ts rollups with trimming according to release type
Output API documentation in a portable format that's easy to integrate with your content pipeline


Best of all, API Extractor is free and open source.  Join the community and create a pull request!





Getting Started

For more details and support resources, please visit: https://api-extractor.com/

API documentation for this package: https://rushstack.io/pages/api/api-extractor/

We pass this README into the model we used to create our embedding. This creates a query embedding for this README.

In [59]:
q = model.encode(query_readme)

We can use `get_nearest_examples` to look for the most similar results to this query. 

In [88]:
scores, retrieved_examples = ds_with_embeddings.get_nearest_examples('embedding', q, k=20000)


Let's take a look at the first result 

In [89]:
retrieved_examples
from sklearn.cluster import DBSCAN
import numpy as np

dbscan_clusters = DBSCAN(min_samples=5).fit(retrieved_examples["embedding"])
print(list(zip(dbscan_clusters.labels_,retrieved_examples["name"])))

[
    (-1, '@microsoft/api-extractor'),
    (-1, '@grafana/api-extractor'),
    (-1, '@dylanvann/api-extractor'),
    (-1, '@microsoft/api-extractor-model'),
    (-1, '@nabh/ts-api-extractor'),
    (-1, '@probed/liberator'),
    (-1, '@princjef/api-documenter'),
    (-1, '@grafana/levitate'),
    (-1, '@taipescripeto/basic'),
    (-1, '@relewise/relewise-client'),
    (-1, '@hackbg/izomorf'),
    (-1, '@quangas/streambird-solana'),
    (-1, '@opndev/util'),
    (-1, '@darwinia/darwinia-polkadotjs-typegen'),
    (-1, '@probedjs/liberator'),
    (-1, '@open-rpc/semantic-release-plugin'),
    (-1, '@createdreamtech/cirrus'),
    (-1, '@caap-store/schemas'),
    (-1, '@gagan-personal/common'),
    (-1, '@taipescripeto/enum-type-guard'),
    (-1, '@ecmascript_monorepo_template/npm_package_typescript_library'),
    (-1, '@qinzisong/path-to-route-path'),
    (-1, '@gridonic/client-services'),
    (-1, '@mtti/microservice'),
    (0, '@danchenkov/api-documenter'),
    (-1, '@kobdev/types'),
    (-1, '@monoid-dev/use-strings'),
    (-1, '@emartech/typescript-example'),
    (-1, '@emartech/awesome-example'),
    (-1, '@emartech/fancy-example'),
    (-1, '@axiasolar/ts'),
    (-1, '@itg/rivet'),
    (-1, '@theapis/sdk'),
    (-1, '@cliqz/metalint'),
    (-1, '@blightio/moar'),
    (-1, '@energybox/react-ui'),
    (1, '@kluseg/trackify'),
    (1, '@alexintosh/assetallocator'),
    (1, '@fangdh/typescript-esbuild-2021'),
    (1, '@gorilla-devs/minecraft'),
    (1, '@sloikaxyz/generator'),
    (-1, '@processversion/api-wrapper'),
    (-1, '@density/lib-api-types'),
    (-1, '@leichtgewicht/pack-ts'),
    (-1, '@dapis/sdk'),
    (-1, '@raha/api-shared'),
    (-1, '@ganbarodigital/ts-lib-error-reporting'),
    (-1, '@jetsam/tooling'),
    (-1, '@githubts/github-languages'),
    (-1, '@nodesecure/ci'),
    (-1, '@sonnguyeninspirelife/types-custom'),
    (-1, '@sinh7b/types-custom'),
    (-1, '@koine/utils'),
    (-1, '@crazyfactory/tinka'),
    (7, '@ow3/dummy-ts-pkg'),
    (-1, '@mccalljoey/lotide'),
    (-1, '@jacquelinesmith190/lotide'),
    (-1, '@revl.com/utils'),
    (3, '@apiglobal/sdk'),
    (-1, '@lab5e/toolbox'),
    (2, '@rpidanny/typescript-package-template'),
    (2, '@abbiamo/seller-theme-utils'),
    (2, '@abbiamo/order-metadata'),
    (2, '@abbiamo/white-label'),
    (2, '@abbiamo/seller-theme'),
    (-1, '@marco-eckstein/js-utils'),
    (-1, '@bscotch/config'),
    (-1, '@alanscodelog/utils'),
    (-1, '@tetcoin/ts'),
    (-1, '@hungry/package-configuration'),
    (-1, '@aphro/runtime-ts'),
    (-1, '@benmvp/cli'),
    (-1, '@snipcart/readts'),
    (-1, '@asl-19/shared-package-configs'),
    (-1, '@ngazicticketingapp/common'),
    (-1, '@abadi199/maybe'),
    (5, '@dwp/eslint-config-typescript'),
    (-1, '@operational/scripts'),
    (-1, '@apisuite/extension-ui-types'),
    (-1, '@angular-package/property'),
    (-1, '@codexteam/typescript-lib-template'),
    (0, '@mattetti/custom-api-documenter'),
    (3, '@apiglobal/typedrequest'),
    (-1, '@aquicore/aq-workflow'),
    (-1, '@stark-tech-space/tookan-node'),
    (-1, '@stark-tech-space/api-package-template'),
    (-1, '@solidbasisventures/intelliwaketsreact'),
    (-1, '@solidbasisventures/intelliwaketsnode'),
    (4, '@k3imagine/permission-handler'),
    (0, '@microsoft/api-documenter'),
    (3, '@gitzone/tswatch'),
    (0, '@googleapis/api-documenter'),
    (0, '@grafana/api-documenter'),
    (0, '@sosuisen/api-documenter'),
    (-1, '@pxlwidgets/tsconfig'),
    (-1, '@guardian/pkgu'),
    (-1, '@kevinmichaelchen/some-protos-ts'),
    (-1, '@telus/create-library'),
    (-1, '@gargrave/ts-module-starter'),
    (-1, '@kmon/schemas'),
    (-1, '@extollo/ui'),
    (-1, '@devlegal/shared-ts'),
    (-1, '@mercari/extract-primitives'),
    (-1, '@khatastroffik/one-ts-for-all'),
    (5, '@ascend-innovations/eslint-config-ts'),
    (-1, '@productboard/tslint-pb'),
    (-1, '@githubts/github-contributions'),
    (4, '@rocketpants/entity'),
    (-1, '@project-300/common-types'),
    

and a lower similarity result

In [62]:
print(retrieved_examples["readme"][9])

TypeScript NPM Package

Scaffold TypeScript npm packages using this template to bootstrap your next library.

This project includes:
- TypeScript
- Rollup
- Microsoft API Extractor
- TypeDoc

Getting Started

Begin via any of the following:


Press the "Use this template" button
Use degit to execute: 


degit github:jasonsturges/typescript-npm-package

Use GitHub CLI to execute: 


gh repo create &lt;name&gt; --template="https://github.com/jasonsturges/typescript-npm-package"

Simply git clone, delete the existing .git folder, and then:

`


Remember to use npm search &lt;term&gt; to avoid naming conflicts in the NPM Registery for your new package name.

Usage

The following tasks are available for npm run:


dev: Run Rollup in watch mode to detect changes to files during development
build: Run Rollup to build a production release distributable
build:types: Run Microsoft API Extractor to rollup a types declaration (d.ts) file 
docs: Run TypeDoc for TSDoc generated documentation in the "docs/" folder
clean: Remove all build artifacts


Development

While test driven development (TDD) would be a good approach to develop your library, also consider creating an app
for prototyping and local testing of your library.

To test within the library, consider using Storybook.  This approach runs a storybook script to load local source 
files for development.

Otherwise, follow these steps to test the package from another project:

From your library project, issue the npm link (or yarn link) command:


npm link


Start Rollup in watch mode:


npm run dev


Create a test app project, by doing the following:

To use your npm package library locally for development, create a new project in a separate folder:


mkdir test-app &amp;&amp; cd test-app
npm init


Take the defaults from npm init; then, add TypeScript:


npm install typescript --save-dev


In the package.json of your test app, add the following two things:
- Set the type of your package to module
- Add a start script to execute your app

json
"type": "module",
"scripts": {
  "start": "tsc &amp;&amp; node index.js",
},


Link to your library using the npm link &lt;name&gt; (or yarn link &lt;name&gt;) command - be sure the &lt;name&gt;
matches your library's package.json name.  For example:


npm link typescript-npm-package


Add a "tsconfig.json" file to your test app that includes a baseUrl and references the paths to your npm linked 
module.  Again, be sure the paths name matches your library's package.json name.  For example:

json
{
  "compilerOptions": {
    "target": "es6",
    "module": "esnext",
    "moduleResolution": "node",
    "strict": true,
    "esModuleInterop": true,
    "baseUrl": ".",
    "paths": {
      "typescript-npm-package": ["node_modules/typescript-npm-package/src"],
      "typescript-npm-package/*": ["node_modules/typescript-npm-package/src/*"]
    }
  }
}


Now, run your app via npm start.

As an example, if your library's "index.ts" file contained:

ts
export const sayHi = () =&gt; {
  console.log("Hi");
};


...your test app would implement an import using your package name, such as:



Development Cleanup

Once development completes, unlink both your library and test app projects.

From your test app project, unlink the library using npm unlink &lt;name&gt; (or yarn unlink &lt;name&gt;) command:


npm unlink typescript-npm-package


From your library project, issue the npm unlink (or yarn unlink) command:


npm unlink


Release Publishing

Update your package.json to next version number, and remember to tag a release.

Once ready to submit your package to the NPM Registry, execute the following tasks via npm (or yarn):


npm run clean &mdash; Assure a clean build
npm run build &mdash; Build the package
npm run build:types &mdash; Build API Extractor d.ts declaration


Assure the proper npm login:


npm login


Submit your package to the registry:


npm publish --access public

The results seem pretty reasonable; the first result appears to be a duplicate. The lower result is for a slightly different task using social media data. 

### Searching 

Being able to find similar model cards is a start but we actually wanted to be able to search directly. Let's see how our results do if we instead search for some terms we might use to try and find suitable models. 

In [48]:
q = model.encode("fake news")

In [49]:
scores, retrieved_examples = ds_with_embeddings.get_nearest_examples('embedding', q, k=10)


In [52]:
print(retrieved_examples["readme"])

[
    'GoodNews\n',
    'Dummy\n',
    'Dummy\n',
    'Dummy\n',
    'dummy\n',
    'Dummy\n',
    'Dummy\n',
    'Fake test\n',
    'truth\n',
    'This is the headline\n'
]

In [51]:
print(retrieved_examples["readme"][1])

Dummy

In [ ]:
print(retrieved_examples["readme"][2])

Not a bad start. Let's try another one

In [ ]:
q = model.encode("financial sentiment")
scores, retrieved_examples = ds_with_embeddings.get_nearest_examples('embedding', q, k=10)
print(retrieved_examples["readme"][0])

In [ ]:
print(retrieved_examples["readme"][1])

In [ ]:
print(retrieved_examples["readme"][9])

These seem like a good starting point. However, we have a few issues relying on model cards alone. Firstly a lot of models don't include them and the quality of them can be mixed. It's maybe a question if we want to use a model that has no model card at all but it is possible that despite a good model card we don't capture everything we'd need for searching in the README. 

## Can we search using model labels? 

We're only working with classification models in this case. For most Pytorch models on the hub, we have a config file. This config usually contains the model's labels. For example, 'positive', 'negative'. 

Maybe instead of relying only on the metadata, we can search 'inside' the model. The labels will often be a helpful reflection of what we're looking for. For example, we want to find a sentiment classification model that roughly puts text into positive or negative sentiment. Again, relying on exact label matches may not work well, but maybe embeddings get around this problem. Let's try it out! 


Let's look at an example label. 

In [ ]:
ds[0]['label']

Since we're expecting labels to match this format lets filter out any that don't fit this structure. 

In [ ]:
ds = ds.filter(lambda example: isinstance(example['label'],list))

### How to create embeddings for our labels?

How should we encode our labels? At the moment, we have a list of labels. One option would be to create an embedding for every single label, which will require us to query multiple embeddings to check for a match. We may also prefer intuatively to have an embedding for the combination of labels. This is because  we probably know more about the model type from all its labels rather than looking at one label at a time. We'll deal with the labels very crudely by joining them on `,` and creating a single string out of all the labels. I'm sure this isn't the best possible approach, but it might be a good place to start testing this idea. 

In [ ]:
ds = ds.map(lambda example: {"string_label": ",".join(example['label'])})

In [ ]:
ds

In [ ]:
ds_with_embeddings = ds.map(lambda example: 
                                           {"label_embedding":encode_readme(example['string_label'])},batched=True, batch_size=16)
                                                                      

In [ ]:
ds_with_embeddings

### Searching with labels 

Now we have some embeddings for the labels, let's try searching. Let's start with an existing set of labels to see how well we can match those. 

In [ ]:
ds_with_embeddings[0]['string_label']

In [ ]:
q = model.encode("negative")

In [ ]:
ds_with_embeddings.add_faiss_index(column='label_embedding')

In [ ]:
scores, retrieved_examples = ds_with_embeddings.get_nearest_examples('label_embedding', q, k=10)


In [ ]:
retrieved_examples['label'][:10]

So far, these results look pretty good, although we haven't done anything we couldn't do with simple string matching. Let's see what happens if we use a slightly more abstract search. 

In [ ]:
q = model.encode("music")

In [ ]:
scores, retrieved_examples = ds_with_embeddings.get_nearest_examples('label_embedding', q, k=10)


In [ ]:
retrieved_examples['label'][:10]

We can see that we get back labels related to music genre:  `['Dance', 'Heavy Metal', 'Hip Hop', 'Indie', 'Pop', 'Rock']`, for our first four results. After that, we get back `['business', 'entertainment', 'sports'],` which might not be too far off what we want if we searched for music.

How about another search term

In [ ]:
q = model.encode("hateful")

In [ ]:
scores, retrieved_examples = ds_with_embeddings.get_nearest_examples('label_embedding', q, k=10)


In [ ]:
retrieved_examples['label'][:10]

Again here we have something quite close to what we'd get with string matching, but we have a bit more flexibility in how we spell/define our labels which might help surface more possible results. 

We'll try a bunch more things...

In [ ]:
def query_labels(query:str):
    q = model.encode(query)
    scores, retrieved_examples = ds_with_embeddings.get_nearest_examples('label_embedding', q, k=10)
    print(f"results for: {query}")
    print(list(zip(retrieved_examples['label'][:10],retrieved_examples['modelId'][:10])))

In [ ]:
query_labels("politics")

In [ ]:
query_labels("fiction, non_fiction")

Let's try the set of emotions one should feel everyday.

In [ ]:
query_labels("worry, disgust, anxiety, fear")

This example of searching for a set of labels might be a better approach in general since the query will better match the format of the intitial search. 

## Conclusion 

It seems like there is some merit in exploring some of these ideas further. There are a lot of improvements that could be made: 
- how the embeddings are created
- removing some 'noise' from the README, for example, by first parsing the Markdown
- improving how the embeddings are created for the labels 
- combining the embeddings in some way either upfront or when queryig
- a bunch of other things... 

If I find some spare time, I plan to dig into these topics a bit further. This is also a nice excuse to play with one of the new open source embedding databases that have popped up in the last couple of years. 
